In [ ]:
import numpy as np
import matplotlib.pyplot as plt

import lumicks.pylake as lk

%matplotlib inline

# Kymographs

[Download this page as a Jupyter notebook](https://lumicks-pylake.readthedocs.io/en/stable/_downloads/da5ae3011d8c5847e1a5811afce1ec21/kymographs.ipynb)

We can download the data needed for this tutorial directly from Zenodo using Pylake. Since we don’t want it in our working folder, we’ll put it in a folder called `"test_data"`:

In [ ]:
filenames = lk.download_from_doi("10.5281/zenodo.7729525", "test_data")

We can use the [`lk.File.kymos`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.File.html#lumicks.pylake.File.kymos) attribute to access the kymographs from a file:

In [ ]:
import lumicks.pylake as lk

file = lk.File("test_data/kymo.h5")
print(file.kymos)  # dict of available kymos: {'16': Kymo(pixels=699)}

This is a regular Python dictionary so we can easily iterate over it:

In [ ]:
# print some details for all kymos in a file
for name, kymo in file.kymos.items():
    print(f"kymograph '{name}', starts at {kymo.start} ns")

# kymograph '16', starts at 1638534513847557200 ns

Or access a particular `Kymo` object directly to work with:

In [ ]:
# use the kymo name as a dict key
kymo = file.kymos["16"]

## Plotting and exporting

Pylake provides a convenience [`plot()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.plot) method to quickly visualize your data. For details and examples see the [Plotting Images](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/plotting_images.html) section.

The kymograph can also be exported to TIFF format:

In [ ]:
kymo.export_tiff("image.tiff")

## Kymo data and details

We can access the raw image data as a [`numpy.ndarray`](None):

In [ ]:
rgb = kymo.get_image("rgb")  # matrix with `shape == (height, width, 3 colors)`
blue = kymo.get_image("blue")  # single color so `shape == (height, width)`

# Plot manually
plt.figure()
plt.imshow(kymo.get_image("green"), aspect="auto", vmax=15)
plt.show()

There are also several properties available for convenient access to the kymograph metadata:

* [`kymo.center_point_um`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.center_point_um) provides a dictionary of the central x, y, and z coordinates of the scan in micrometers relative to the brightfield field of view
  
* [`kymo.size_um`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.size_um) provides a list of scan sizes in micrometers along the axes of the scan
  
* [`kymo.pixelsize_um`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.pixelsize_um) provides the pixel size in micrometers
  
* [`kymo.pixels_per_line`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.pixels_per_line) provides the number of pixels in each line of the kymograph
  
* [`kymo.fast_axis`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.fast_axis) provides the axis that was scanned (x or y)
  
* [`kymo.line_time_seconds`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.line_time_seconds) provides the time between successive lines
  
* [`kymo.pixel_time_seconds`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.pixel_time_seconds) provides the pixel dwell time.
  
* [`kymo.duration`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.duration) provides the full duration of the kymograph in seconds. This is equivalent to the number of scan lines times `line_time_seconds`.
  
## Slicing, cropping & flipping

Kymographs can  be sliced in order to obtain a specific time range. For example, one can plot the region of the kymograph between 130 and 160 seconds using:

In [ ]:
plt.figure()
kymo["130s":"160s"].plot("rgb", adjustment=lk.ColorAdjustment(0, 98, mode="percentile"))
plt.show()

It is possible to crop a kymograph to a specific coordinate range, by using the function [`Kymo.crop_by_distance()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.crop_by_distance). For example, we can crop the region from `9.5` micron to `26` microns using the following command:

In [ ]:
plt.figure()
kymo.crop_by_distance(9.5, 26).plot("rgb", aspect="auto", adjustment=lk.ColorAdjustment(0, 98, mode="percentile"))
plt.show()

If we know the bead diameter, we can automatically crop the kymo to an estimate of the bead edges using [`crop_beads()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.crop_beads). This can be convenient when batch processing many kymographs:

In [ ]:
plt.figure()
kymo.crop_beads(4.84, algorithm="brightness").plot("rgb", aspect="auto", adjustment=lk.ColorAdjustment(0, 98, mode="percentile"))
plt.show()

<div class="alert alert-block alert-info"><b>Note: </b>Note, slicing in time is currently only supported for unprocessed kymographs. If you want to both crop and slice a kymo, the order of operations is important – you need to slice before cropping:</div>

In [ ]:
kymo_sliced = kymo["130s":"160s"]
kymo_cropped = kymo_sliced.crop_by_distance(9.5, 26)

plt.figure()
kymo_cropped.plot("rgb", adjustment=lk.ColorAdjustment(0, 99.9, mode="percentile"))
plt.show()

<div class="alert alert-block alert-info"><b>Note: </b>If you try to slice a kymograph that has already been cropped, a `NotImplementedError` will be raised.</div>

Finally, we can also flip a kymograph along its positional axis using [`flip()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.flip). This returns a new (but flipped) [`Kymo`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo):

In [ ]:
kymo_flipped = kymo.flip()

plt.figure()
plt.subplot(211)
kymo.plot("rgb", adjustment=lk.ColorAdjustment(0, 98, mode="percentile"))

plt.subplot(212)
kymo_flipped.plot("rgb", adjustment=lk.ColorAdjustment(0, 98, mode="percentile"))

plt.tight_layout()
plt.show()

## Calibrating to base pairs

By default, kymographs are constructed with units of microns for the position axis. If, however, the kymograph spans a known length of DNA (here for example, lambda DNA) we can calibrate the position axis to kilobase pairs (kbp):

In [ ]:
kymo_kbp = kymo_cropped.calibrate_to_kbp(48.502)

Now if we plot the image, the y-axis will be labeled in kbp:

In [ ]:
plt.figure()
kymo_kbp.plot("green")
plt.show()

These units are also carried forward to any downstream operations such as kymotracking algorithms and MSD analysis.

<div class="alert alert-block alert-danger"><b>Warning: </b>Currently this is a static calibration, meaning it is only valid if the traps do not change position during the time of the kymograph.</div>

<div class="alert alert-block alert-danger"><b>Warning: </b>Also, the accuracy of the calibration is dependent on how the kymo is cropped. If you crop the kymo by visually estimating the bead edges, the resulting position should be taken as approximate.</div>

## Interactive slicing, cropping & calibration

We can also interactively slice, crop, and calibrate kymographs using [`crop_and_calibrate()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.crop_and_calibrate):

In [ ]:
widget = kymo.crop_and_calibrate(channel="rgb", tether_length_kbp=48.502, aspect="auto", adjustment=lk.ColorAdjustment(0, 99.5, mode="percentile"))

Simply click and drag the rectangle selector to the desired ROI. We can then access the edited kymograph with:

In [ ]:
new_kymo = widget.kymo

plt.figure()
new_kymo.plot("green")
plt.show()

If the optional `tether_length_kbp` argument is supplied, the kymograph is automatically calibrated to the desired length in kilobase pairs. If this argument is missing (the default value `None`) the edited kymograph is only sliced and cropped.

## Downsampling

We can downsample a kymograph in time by invoking:

In [ ]:
kymo_ds_time = kymo_cropped.downsampled_by(time_factor=2)

Or in space by invoking:

In [ ]:
kymo_ds_position = kymo_cropped.downsampled_by(position_factor=2)

Or both:

In [ ]:
kymo_ds = kymo_cropped.downsampled_by(time_factor=2, position_factor=2)
adjustment = lk.ColorAdjustment(0, 30, mode="absolute")

plt.figure()

plt.subplot(221)
kymo_cropped.plot("green", adjustment=adjustment)
plt.title("original")
plt.subplot(222)
kymo_ds_time.plot("green", adjustment=adjustment)
plt.title("downsampled time")
plt.subplot(223)
kymo_ds_position.plot("green", adjustment=adjustment)
plt.title("downsampled position")
plt.subplot(224)
kymo_ds.plot("green", adjustment=adjustment)
plt.title("downsampled both")

plt.tight_layout()
plt.show()

Note however, that not all functionalities are present anymore when downsampling a kymograph over time. This is because the downsampling occurs over non-contiguous sections of time (across multiple scan lines) and therefore each pixel no longer has an identifiable time. For example, we can no longer access the per pixel timestamps:

In [ ]:
# this cell will raise a `NotImplementedError`
kymo_ds.timestamps

Additionally, a downsampled kymograph cannot be sliced (same as cropped kymographs mentioned above). Therefore you should first slice the kymograph and then downsample.

## Correlating with force

We can downsample channel data according to the lines in a kymo. We can use [`line_timestamp_ranges()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.line_timestamp_ranges) for this:

In [ ]:
line_timestamp_ranges = kymo.line_timestamp_ranges()

This returns a list of start and stop timestamps that can be passed directly to [`downsampled_to()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.channel.Slice.html#lumicks.pylake.channel.Slice.downsampled_to), which will then return a [`Slice`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.channel.Slice.html#lumicks.pylake.channel.Slice) with a datapoint per line:

In [ ]:
force = file.force1x
downsampled = force.downsampled_over(line_timestamp_ranges)

plt.figure()
force.plot(label="high frequency")
downsampled.plot(start=force.start, label="downsampled like kymo")
plt.legend()
plt.show()

There is also a convenience function [`plot_with_force()`](https://lumicks-pylake.readthedocs.io/en/stable/tutorial/../_api/lumicks.pylake.kymo.Kymo.html#lumicks.pylake.kymo.Kymo.plot_with_force) to plot a kymograph along with a downsampled force trace:

In [ ]:
kymo.plot_with_force("1x", "green", adjustment=lk.ColorAdjustment(0, 15))

This will average the forces over each Kymograph line and plot them in a correlated fashion. The function can also take a dictionary of extra arguments to customize the kymograph plot. These parameter values get forwarded to [`matplotlib.pyplot.imshow()`](None).